In [2]:
import arcpy
import os
import pandas as pd
import shutil
import smtplib
import traceback
from arcgis.features import GeoAccessor, GeoSeriesAccessor
from email.message import EmailMessage
from zipfile import ZipFile

# this process probably needs to be run from a scripting server, using a service account
# instead of a workstation from a user account

def send_email(message_or_traceback_here, status, script_name="Google to SDE", list_recipients=["justin.cozart@dentoncad.com"]):
    """A standard email function, insert list of recipients, subject, etc."""
    message = EmailMessage()
    message.set_content(f"{message_or_traceback_here}")
    message["Subject"] = f"{script_name} - {status}"
    message["From"] = list_recipients[0]
    message["To"] = ", ".join(list_recipients)
    smtp_server = smtplib.SMTP("sm.dentoncad.com")
    smtp_server.send_message(message)
    smtp_server.quit()

def initiate_geodatabase(export_gdb, yesterday_gdb, folder_export):
    """Archive and Re-Create Geodatabase for Export"""
    print("Beginning Geodatabase Operations:")
    arcpy.env.workspace = folder_export
    if arcpy.Exists(f"{yesterday_gdb}.gdb"):
        print("\n\tDeleting stale geodatabase")
        arcpy.management.Delete(f"{yesterday_gdb}.gdb")
    if arcpy.Exists(f"{export_gdb}.gdb"):
        print("\n\tBacking up yesterday's geodatabase")
        arcpy.management.Rename(f"{export_gdb}.gdb", "yesterday_geodatabase")
        print("\tInitializing new file geodatabase")
        arcpy.management.CreateFileGDB(folder_export, "nightly_geodatabase")
    else:
        print("\n\tInitializing new file geodatabase")
        arcpy.management.CreateFileGDB(folder_export, "nightly_geodatabase")

def convert_featureclasses_to_gdb(sde_parcels, sde_subdivisions, path_pacs, pacs_appraisal, export_gdb):
    """Convert SDE and PACS data to File Geodatabase"""
    print("\tSending database features and tables to file geodatabase for processing")
    arcpy.conversion.FeatureClassToFeatureClass(sde_parcels, f"{export_gdb}.gdb", "Parcels")
    arcpy.conversion.FeatureClassToFeatureClass(sde_subdivisions, f"{export_gdb}.gdb", "Subdivisions")
    arcpy.env.workspace = path_pacs
    sdf_cama = pd.DataFrame.spatial.from_table(pacs_appraisal, null_value=-9999)
    sdf_cama = sdf_cama.replace( ["-9999", -9999] , None)
    sdf_cama.spatial.to_table(f"{export_gdb}.gdb\Appraisals")

def join_parcels_to_pacs(fc_parcels, join_field_parcels, tbl_appraisal, join_field_appraisals,export_gdb):
    """Join Parcels Data to PACS data inside File Geodatabase"""
    print("\tJoining Parcels to CAMA data")
    arcpy.env.workspace = f"{export_gdb}.gdb"
    #this is broken right now
    #the following lines are a workaround
    #    arcpy.management.JoinField(fc_parcels, join_field_parcels, tbl_appraisal, join_field_appraisals)
    sdf_parcels = pd.DataFrame.spatial.from_featureclass(fc_parcels)
    sdf_appraisal = pd.DataFrame.spatial.from_table(tbl_appraisal, null_value=-9999)
    sdf_appraisal = sdf_appraisal.replace( ["-9999", -9999] , None)
    #if the data frames do not have a join column named the same you'll need to do the following
    #    sdf_something[join_field_to_match_here] = sdf_something[the_field_name_that_doesnt_currently_match]
    #we join the fields, and add a suffix to prevent overlaps, we then drop the duplicates and rename the suffix columns
    sdf_parcels.join(sdf_appraisal, on=join_field_parcels, how='left', lsuffix='1')
    sdf_enriched.drop(labels=["OBJECTID", "prop_id"], axis=1, inplace=True)
    sdf_enriched.rename(columns={"OBJECTID1": "OBJECTID", "prop_id1": "prop_id"}, inplace=True)
    sdf_enriched.spatial.to_featureclass(fc_parcels)

def remove_tracking_fields(fc_parcels):
    """Remove Editor Tracking Fields from a Feature Class"""
    print("\tFinding unwanted fields")
    field_names = [f.name for f in arcpy.ListFields(fc_parcels)]
    delete_fields = []
    for field in field_names:
        # test for unwanted fields, modifies field list to use as input to DeleteField()
        if "created_" in field or "last_" in field or "prop_id_1" in field:
            delete_fields.append(field)
    print(f"\tRemoving the following fields:\n\t\t{delete_fields}")
    arcpy.management.DeleteField(fc_parcels, delete_fields)
    print("\tAll File Geodatabase Operations Complete")

def export_table_to_csv(export_csv, yesterday_csv, tbl_appraisal):
    """Archives Previous CSV, Copies PACS File Geodatabase Table to CSV"""
    print("\nBeginning CSV Operations:")
    print("\tBacking up yesterday's CSV")
    if os.path.isfile(f"{export_csv}.csv"):
        shutil.copyfile(f"{export_csv}.csv", f"{yesterday_csv}.csv")
    print("\tExporting CAMA data to CSV")
    sdf_cama = pd.DataFrame.spatial.from_table(tbl_appraisal, null_value=-9999)
    sdf_cama = sdf_cama.replace( ["-9999", -9999] , None)
    csv_cama = sdf_cama.to_csv(f"{export_csv}.csv")
    del sdf_cama
    print("\tAll CSV Operations Complete")

def zipping_utilities(export_gdb, yesterday_gdb, export_csv, yesterday_csv):
    """Archive Previous Zipped Folders, Zips Current Data"""
    print("\nBeginning Zip Operations:")
    if os.path.isfile(f"{export_gdb}.gdb.zip"):
        print(f"\tBacking up yesterday's zipped geodatabase: {export_gdb}.gdb.zip")
        shutil.copyfile(f"{export_gdb}.gdb.zip", f"{yesterday_gdb}.gdb.zip")
    if os.path.isfile(f"{export_csv}.zip"):
        print(f"\tBacking up yesterday's zipped csv: {export_csv}.zip")
        shutil.copyfile(f"{export_csv}.zip", f"{yesterday_csv}.zip")
    print("\tWriting current geodatabase")
    shutil.make_archive(base_name=f"{export_gdb}.gdb", format="zip",root_dir=f"{export_gdb}.gdb")
    print("\tWriting current csv")
    with ZipFile(f"{export_csv}.zip", 'w') as zipf:
        zipf.write(f"{export_csv}.csv", arcname="nightly_appraisals.csv")
    shutil.copyfile(f"{yesterday_gdb}.gdb.zip", f"{gdrive_gdb}.gdb.zip")
    shutil.copyfile(f"{export_gdb}.gdb.zip", f"{gdrive_yesterday_gdb}.gdb.zip")
    shutil.copyfile(f"{yesterday_csv}.zip", f"{gdrive_csv}.zip")
    shutil.copyfile(f"{export_csv}.zip", f"{gdrive_yesterday_csv}.zip")
    print("\tAll Zip Operations Complete")



folder_export = r"C:\Users\justin.cozart\_Nightly_Exports"
folder_connections = r"C:\Users\justin.cozart\AppData\Roaming\Esri\ArcGISPro\Favorites"
export_gdb = f"{folder_export}\\nightly_geodatabase"
export_csv = f"{folder_export}\\nightly_appraisals"
yesterday_gdb = f"{folder_export}\\yesterday_geodatabase"
yesterday_csv = f"{folder_export}\\yesterday_appraisals"
dict_exports = {
    "nightly_geodatabase.gdb.zip" : f"{export_gdb}.gdb.zip",
    "nightly_appraisals.zip" : f"{export_csv}.zip",
    "yesterday_geodatabase.gdb.zip" : f"{yesterday_gdb}.gdb.zip",
    "yesterday_appraisals.zip" : f"{yesterday_csv}.zip"
    }
folder_gdrive = r"M:\GIS DATADOWNLOADS"
gdrive_gdb = f"{folder_gdrive }\\nightly_geodatabase"
gdrive_csv = f"{folder_gdrive }\\nightly_appraisals"
gdrive_yesterday_gdb = f"{folder_gdrive }\\yesterday_geodatabase"
gdrive_yesterday_csv = f"{folder_gdrive }\\yesterday_appraisals"

path_sde = f"{folder_connections}\dserv-gis01.sde"
path_pacs = r"C:\Users\justin.cozart\AppData\Roaming\ESRI\Desktop10.7\ArcCatalog\APSQL.sde"
sde_parcels = f"{path_sde}\dentonsde.sde.LandRecords\dentonsde.sde.Parcel"
sde_subdivisions = f"{path_sde}\dentonsde.sde.LandRecords\dentonsde.sde.Subdivision"
pacs_appraisal = f"{path_pacs}\pacs_oltp.dbo.DCADData_vw_NEW"

fc_parcels = f"{export_gdb}.gdb\Parcels"
fc_subdivisions = f"{export_gdb}.gdb\Subdivisions"
tbl_appraisal = f"{export_gdb}.gdb\Appraisals"
join_field_parcels = "prop_id"
join_field_appraisals = "prop_id"

# initiate geodatabase
initiate_geodatabase(export_gdb, yesterday_gdb, folder_export)
# convert all database features to file geodatabase for processing
convert_featureclasses_to_gdb(sde_parcels, sde_subdivisions, path_pacs, pacs_appraisal, export_gdb)
# join to cama table by prop-id, discard non-matches
join_parcels_to_pacs(fc_parcels, join_field_parcels, tbl_appraisal, join_field_appraisals, export_gdb)
# delete edit tracking fields
remove_tracking_fields(fc_parcels)
# export cama data to csv in project folder
export_table_to_csv(export_csv, yesterday_csv, tbl_appraisal)
# zip up contents
zipping_utilities(export_gdb, yesterday_gdb, export_csv, yesterday_csv)

Beginning Geodatabase Operations:

	Deleting stale geodatabase

	Backing up yesterday's geodatabase
	Initializing new file geodatabase
	Sending database features and tables to file geodatabase for processing
	Joining Parcels to CAMA data


ValueError: columns overlap but no suffix specified: Index(['prop_id', 'owner_name', 'addr_line1', 'addr_line2', 'addr_line3',
       'addr_city', 'addr_state', 'addr_zip', 'legal_desc', 'abs_subdv_cd',
       'abs_subdv_desc', 'block', 'tract_or_lot', 'legal_acreage', 'land_sqft',
       'living_area', 'exemptions', 'cad_zoning', 'state_cd', 'yr_blt',
       'land_type_cd', 'city', 'school', 'special_dist', 'situs_num',
       'situs_street_prefx', 'situs_street', 'situs_street_sufix',
       'situs_city', 'situs_state', 'situs_zip', 'situs', 'prop_val_yr',
       'cert_appr_val', 'cert_asses_val', 'cert_mkt_val', 'main_imprv',
       'main_imprv_val', 'ag_exempt'],
      dtype='object')